In [1]:
import utils as utils
import numpy as np
import karoke

from lyrics import timestamped_lyrics
from audio import download_audio

loading model... done


In [2]:
def crosslyrics(
    youtube_url: str, track_id: str, n: int = 5, tta: bool = True
) -> tuple[float, np.ndarray, list[np.ndarray]]:
    # Audio
    info = download_audio(youtube_url)
    sr, x = utils.read(info["file"])
    x = x.astype(np.float32)

    # Lyrics
    times, lines = np.array(
        [[t, l] for t, l in timestamped_lyrics(track_id) if "(" and ")" not in l]
    ).T  # [ms], [lyric]
    times = (times.astype(int) * (sr / 1000)).astype(int)  # [samples]
    lines = lines.astype(str, copy=False)

    # Sample indices for n lyric triplets
    rand_i = np.random.choice(lines.size - 3, n)  # i, i + 1, i + 2

    return (
        sr,
        np.stack(
            (lines[rand_i], lines[rand_i + 1], lines[rand_i + 2])
        ).T,  # Lyric triplets
        [
            np.concatenate(
                (
                    x[times[i] : times[i + 1]],
                    karoke.remove_vocals(x[times[i + 1] : times[i + 2]].T, tta).astype(
                        np.float32
                    ),
                    x[times[i + 2] : times[i + 3]],
                ),
            ).T
            for i in rand_i
        ],  # Concatenated triplets of samples
    )

In [3]:
sr, lyrics, samples = crosslyrics(
    "https://www.youtube.com/watch?v=asew9BF1wdw",
    "2Zo1PcszsT9WQ0ANntJbID",
    n=2,
    tta=False,
)

[youtube] Extracting URL: https://www.youtube.com/watch?v=asew9BF1wdw
[youtube] asew9BF1wdw: Downloading webpage
[youtube] asew9BF1wdw: Downloading ios player API JSON
[youtube] asew9BF1wdw: Downloading android player API JSON
[youtube] asew9BF1wdw: Downloading m3u8 information
[info] asew9BF1wdw: Downloading 1 format(s): 251
[download] Destination: ./Sabrina Carpenter - Feather (Lyric Video).webm
[download] 100% of    2.87MiB in 00:00:00 at 17.45MiB/s  
[ExtractAudio] Destination: ./Sabrina Carpenter - Feather (Lyric Video).wav
Deleting original file ./Sabrina Carpenter - Feather (Lyric Video).webm (pass -k to keep)
(2, 233280)
stft of input x... done


100%|██████████| 1/1 [00:04<00:00,  4.45s/it]


validating output directory... done
inverse stft of instruments... done
(2, 120960)
stft of input x... done


100%|██████████| 1/1 [00:01<00:00,  1.70s/it]

validating output directory... done
inverse stft of instruments... done


In [4]:
utils.sounds(
    samples,
    sr,
    [str(l) for l in lyrics],
    "crosslyrics",
)

crosslyrics
